In [19]:
import numpy as np
import open3d as o3d
import os 
from tqdm.notebook import tqdm
import torch
import torch.optim as optim

In [22]:
torch.cuda.is_available()

True

In [3]:
dirt = 'D:/DataSet/shape_net_core_uniform_samples_2048/'
folders = os.listdir(dirt)

In [4]:
files = []
for fold in folders:
    direc = dirt + fold
    for file in os.listdir(direc):
        files.append(direc + '/' + file)

In [5]:
len(files)

57449

In [6]:
files[0]

'D:/DataSet/shape_net_core_uniform_samples_2048/02691156/10155655850468db78d106ce0a280f87.ply'

In [7]:
# Read .ply file
input_file = files[10]
pcd = o3d.io.read_point_cloud(input_file) # Read the point cloud

# Visualize the point cloud within open3d
o3d.visualization.draw_geometries([pcd]) 
# Convert open3d format to numpy array
# Here, you have the point cloud in numpy format. 
point_cloud_in_numpy = np.asarray(pcd.points) 

In [9]:
len(point_cloud_in_numpy)

2048

In [10]:
class TrainDataset(torch.utils.data.Dataset):
    def __init__(self):
        super().__init__()
        pts = []
        for input_file in tqdm(files):
            pcd = o3d.io.read_point_cloud(input_file)
            point_cloud_in_numpy = np.asarray(pcd.points) 
            pts.append(point_cloud_in_numpy)  
            
        #maxlen = max([len(x) for x in pts])
        #pad_pts = np.zeros((len(pts), maxlen, 3))    
        self.pts = pts
        
    def __len__(self):
        return len(self.pts)
    def __getitem__(self, idx):
        pts = self.pts[idx]
        pts = torch.tensor(pts.T).float().contiguous()
        return pts

In [16]:
%load_ext autoreload
%autoreload 2
from PointGAN import *

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [28]:
dataset = TrainDataset()
train_loader = DataLoader(dataset, batch_size=64, shuffle=True, pin_memory=True, drop_last=True)

  0%|          | 0/57449 [00:00<?, ?it/s]

In [30]:
inputs = next(iter(train_loader))

In [31]:
inputs.shape

torch.Size([64, 3, 2048])

In [33]:
classifier = Discriminator()
gen = Generator()

def weights_init(m):
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        m.weight.data.normal_(0.0, 0.02)
    elif classname.find('BatchNorm') != -1:
        m.weight.data.normal_(1.0, 0.02)
        m.bias.data.fill_(0)

classifier.apply(weights_init)
gen.apply(weights_init)

classifier.cuda()
gen.cuda()

optimizerD = optim.Adagrad(classifier.parameters(), lr = 0.001)
optimizerG = optim.Adagrad(gen.parameters(), lr = 0.001)

num_batch = len(dataset)/64

for epoch in tqdm(range(100)):
    for i, data in enumerate(train_loader, 0):
        optimizerD.zero_grad()
        points = data
        points = Variable(points)

        bs = points.size()[0]
        target = Variable(torch.from_numpy(np.ones(bs,).astype(np.int64))).cuda()
        #points = points.transpose(2,1)
        points = points.cuda()
        #print(points.size())

        pred, trans = classifier(points)
        loss1 = F.nll_loss(pred, target)

        sim_noise = Variable(torch.randn(bs, 128)).cuda()
        fake = gen(sim_noise)
        fake_target = Variable(torch.from_numpy(np.zeros(bs,).astype(np.int64))).cuda()
        pred2, trans2 = classifier(fake)

        loss2 = F.nll_loss(pred2, fake_target)

        lossD = (loss1 + loss2)/2
        lossD.backward()
        #print(pred, target)
        optimizerD.step()

        optimizerG.zero_grad()
        sim_noise = Variable(torch.randn(bs, 128)).cuda()
        points = gen(sim_noise)
        pred, trans = classifier(points)
        target = Variable(torch.from_numpy(np.ones(bs,).astype(np.int64))).cuda()
        #print(pred, target)
        lossG = F.nll_loss(pred, target)
        lossG.backward()
        optimizerG.step()

        print('[%d: %d/%d] train lossD: %f lossG: %f' %(epoch, i, num_batch, lossD.data, lossG.data))

  0%|          | 0/100 [00:00<?, ?it/s]

[0: 0/897] train lossD: 0.814060 lossG: 4.886608
[0: 1/897] train lossD: 1.209804 lossG: 0.000600
[0: 2/897] train lossD: 3.824637 lossG: 1.490412
[0: 3/897] train lossD: 0.635481 lossG: 0.514528
[0: 4/897] train lossD: 0.716977 lossG: 2.813610
[0: 5/897] train lossD: 0.803743 lossG: 0.407717
[0: 6/897] train lossD: 0.755677 lossG: 2.370605
[0: 7/897] train lossD: 0.734951 lossG: 0.838893
[0: 8/897] train lossD: 0.584698 lossG: 1.253054
[0: 9/897] train lossD: 0.555642 lossG: 0.838745
[0: 10/897] train lossD: 0.534049 lossG: 1.716863
[0: 11/897] train lossD: 0.556906 lossG: 0.848845
[0: 12/897] train lossD: 0.519934 lossG: 1.495989
[0: 13/897] train lossD: 0.528643 lossG: 0.854985
[0: 14/897] train lossD: 0.518160 lossG: 1.441529
[0: 15/897] train lossD: 0.490920 lossG: 0.880660
[0: 16/897] train lossD: 0.486267 lossG: 1.683226
[0: 17/897] train lossD: 0.501686 lossG: 0.796993
[0: 18/897] train lossD: 0.533897 lossG: 1.802954
[0: 19/897] train lossD: 0.549011 lossG: 0.789768
[0: 20/897

[0: 164/897] train lossD: 0.125421 lossG: 4.882444
[0: 165/897] train lossD: 0.200897 lossG: 2.173248
[0: 166/897] train lossD: 0.216338 lossG: 5.848753
[0: 167/897] train lossD: 0.394947 lossG: 3.615323
[0: 168/897] train lossD: 0.155742 lossG: 2.370235
[0: 169/897] train lossD: 0.173058 lossG: 4.288714
[0: 170/897] train lossD: 0.173870 lossG: 2.821623
[0: 171/897] train lossD: 0.239141 lossG: 3.560066
[0: 172/897] train lossD: 0.214364 lossG: 2.298043
[0: 173/897] train lossD: 0.284536 lossG: 4.465663
[0: 174/897] train lossD: 0.384843 lossG: 2.270949
[0: 175/897] train lossD: 0.365685 lossG: 3.541559
[0: 176/897] train lossD: 0.281391 lossG: 1.480471
[0: 177/897] train lossD: 0.332522 lossG: 3.896468
[0: 178/897] train lossD: 0.338150 lossG: 1.919879
[0: 179/897] train lossD: 0.306752 lossG: 4.417982
[0: 180/897] train lossD: 0.257086 lossG: 2.417677
[0: 181/897] train lossD: 0.282657 lossG: 3.571238
[0: 182/897] train lossD: 0.277509 lossG: 1.776405
[0: 183/897] train lossD: 0.343

[0: 326/897] train lossD: 0.186767 lossG: 4.225644
[0: 327/897] train lossD: 0.179519 lossG: 2.088545
[0: 328/897] train lossD: 0.169722 lossG: 3.015947
[0: 329/897] train lossD: 0.179497 lossG: 1.786556
[0: 330/897] train lossD: 0.233668 lossG: 3.527089
[0: 331/897] train lossD: 0.176668 lossG: 1.793000
[0: 332/897] train lossD: 0.188235 lossG: 3.469552
[0: 333/897] train lossD: 0.219892 lossG: 1.602077
[0: 334/897] train lossD: 0.277083 lossG: 4.742351
[0: 335/897] train lossD: 0.410199 lossG: 2.136118
[0: 336/897] train lossD: 0.172813 lossG: 3.141827
[0: 337/897] train lossD: 0.166676 lossG: 2.514630
[0: 338/897] train lossD: 0.147351 lossG: 3.559298
[0: 339/897] train lossD: 0.190204 lossG: 2.709188
[0: 340/897] train lossD: 0.157537 lossG: 2.457527
[0: 341/897] train lossD: 0.151975 lossG: 2.155280
[0: 342/897] train lossD: 0.156159 lossG: 4.023612
[0: 343/897] train lossD: 0.204872 lossG: 1.914821
[0: 344/897] train lossD: 0.176099 lossG: 4.237906
[0: 345/897] train lossD: 0.277

[0: 488/897] train lossD: 0.122513 lossG: 3.428092
[0: 489/897] train lossD: 0.095081 lossG: 3.245010
[0: 490/897] train lossD: 0.090850 lossG: 2.340950
[0: 491/897] train lossD: 0.125367 lossG: 4.850351
[0: 492/897] train lossD: 0.166138 lossG: 2.260983
[0: 493/897] train lossD: 0.089610 lossG: 3.549008
[0: 494/897] train lossD: 0.089348 lossG: 2.433322
[0: 495/897] train lossD: 0.103521 lossG: 3.179344
[0: 496/897] train lossD: 0.098038 lossG: 3.071982
[0: 497/897] train lossD: 0.082612 lossG: 2.509242
[0: 498/897] train lossD: 0.111645 lossG: 5.227865
[0: 499/897] train lossD: 0.227498 lossG: 2.002940
[0: 500/897] train lossD: 0.149358 lossG: 5.053900
[0: 501/897] train lossD: 0.178724 lossG: 1.907539
[0: 502/897] train lossD: 0.215898 lossG: 5.660402
[0: 503/897] train lossD: 0.452271 lossG: 2.738781
[0: 504/897] train lossD: 0.139199 lossG: 4.503682
[0: 505/897] train lossD: 0.244168 lossG: 2.643479
[0: 506/897] train lossD: 0.098603 lossG: 4.355335
[0: 507/897] train lossD: 0.086

...

[99: 159/897] train lossD: 0.106398 lossG: 3.017739
[99: 160/897] train lossD: 0.130858 lossG: 3.150342
[99: 161/897] train lossD: 0.159482 lossG: 2.262164
[99: 162/897] train lossD: 0.091342 lossG: 2.366946
[99: 163/897] train lossD: 0.084956 lossG: 3.695854
[99: 164/897] train lossD: 0.135141 lossG: 2.558839
[99: 165/897] train lossD: 0.173945 lossG: 4.289755
[99: 166/897] train lossD: 0.038492 lossG: 4.456296
[99: 167/897] train lossD: 0.094027 lossG: 2.975784
[99: 168/897] train lossD: 0.194603 lossG: 2.286031
[99: 169/897] train lossD: 0.123334 lossG: 3.040477
[99: 170/897] train lossD: 0.087793 lossG: 3.468358
[99: 171/897] train lossD: 0.094326 lossG: 4.054457
[99: 172/897] train lossD: 0.196697 lossG: 2.761502
[99: 173/897] train lossD: 0.109788 lossG: 3.353786
[99: 174/897] train lossD: 0.114210 lossG: 2.813989
[99: 175/897] train lossD: 0.093513 lossG: 3.990211
[99: 176/897] train lossD: 0.133789 lossG: 2.790740
[99: 177/897] train lossD: 0.147902 lossG: 2.916698
[99: 178/897

[99: 317/897] train lossD: 0.146103 lossG: 4.593355
[99: 318/897] train lossD: 0.205769 lossG: 2.560497
[99: 319/897] train lossD: 0.141892 lossG: 3.528480
[99: 320/897] train lossD: 0.060787 lossG: 3.427966
[99: 321/897] train lossD: 0.116822 lossG: 3.718365
[99: 322/897] train lossD: 0.129568 lossG: 2.320590
[99: 323/897] train lossD: 0.138167 lossG: 3.139426
[99: 324/897] train lossD: 0.144657 lossG: 2.376344
[99: 325/897] train lossD: 0.105002 lossG: 3.747587
[99: 326/897] train lossD: 0.132337 lossG: 3.200015
[99: 327/897] train lossD: 0.101052 lossG: 2.665751
[99: 328/897] train lossD: 0.122032 lossG: 2.675938
[99: 329/897] train lossD: 0.197209 lossG: 1.888010
[99: 330/897] train lossD: 0.183158 lossG: 5.385559
[99: 331/897] train lossD: 0.185622 lossG: 3.367772
[99: 332/897] train lossD: 0.146519 lossG: 2.690851
[99: 333/897] train lossD: 0.152120 lossG: 3.509251
[99: 334/897] train lossD: 0.294594 lossG: 2.973584
[99: 335/897] train lossD: 0.162760 lossG: 2.736219
[99: 336/897

[99: 475/897] train lossD: 0.052177 lossG: 3.275108
[99: 476/897] train lossD: 0.225183 lossG: 2.539890
[99: 477/897] train lossD: 0.093301 lossG: 2.695201
[99: 478/897] train lossD: 0.182725 lossG: 2.553857
[99: 479/897] train lossD: 0.105244 lossG: 2.849900
[99: 480/897] train lossD: 0.219445 lossG: 2.369697
[99: 481/897] train lossD: 0.116541 lossG: 5.123157
[99: 482/897] train lossD: 0.259168 lossG: 2.142852
[99: 483/897] train lossD: 0.166578 lossG: 3.348892
[99: 484/897] train lossD: 0.183664 lossG: 2.649566
[99: 485/897] train lossD: 0.151417 lossG: 3.195013
[99: 486/897] train lossD: 0.213058 lossG: 2.785490
[99: 487/897] train lossD: 0.116996 lossG: 3.466352
[99: 488/897] train lossD: 0.097292 lossG: 2.955602
[99: 489/897] train lossD: 0.138811 lossG: 3.310422
[99: 490/897] train lossD: 0.270707 lossG: 2.042968
[99: 491/897] train lossD: 0.158714 lossG: 3.327491
[99: 492/897] train lossD: 0.219689 lossG: 2.203703
[99: 493/897] train lossD: 0.081437 lossG: 2.325556
[99: 494/897

[99: 633/897] train lossD: 0.080712 lossG: 3.242434
[99: 634/897] train lossD: 0.113743 lossG: 3.397502
[99: 635/897] train lossD: 0.091542 lossG: 2.917450
[99: 636/897] train lossD: 0.152279 lossG: 3.025533
[99: 637/897] train lossD: 0.133820 lossG: 3.086835
[99: 638/897] train lossD: 0.099554 lossG: 2.641782
[99: 639/897] train lossD: 0.174318 lossG: 3.150450
[99: 640/897] train lossD: 0.198704 lossG: 2.568232
[99: 641/897] train lossD: 0.135659 lossG: 3.670420
[99: 642/897] train lossD: 0.092396 lossG: 3.566839
[99: 643/897] train lossD: 0.114200 lossG: 2.697494
[99: 644/897] train lossD: 0.166188 lossG: 3.750222
[99: 645/897] train lossD: 0.079574 lossG: 3.163273
[99: 646/897] train lossD: 0.087426 lossG: 3.059101
[99: 647/897] train lossD: 0.173672 lossG: 3.560971
[99: 648/897] train lossD: 0.069116 lossG: 3.432454
[99: 649/897] train lossD: 0.098380 lossG: 3.193297
[99: 650/897] train lossD: 0.140371 lossG: 2.862307
[99: 651/897] train lossD: 0.102021 lossG: 3.083531
[99: 652/897

[99: 791/897] train lossD: 0.078031 lossG: 3.227370
[99: 792/897] train lossD: 0.090338 lossG: 2.993397
[99: 793/897] train lossD: 0.134763 lossG: 3.123350
[99: 794/897] train lossD: 0.081658 lossG: 3.344285
[99: 795/897] train lossD: 0.141396 lossG: 2.625702
[99: 796/897] train lossD: 0.090195 lossG: 2.752576
[99: 797/897] train lossD: 0.096534 lossG: 3.573050
[99: 798/897] train lossD: 0.044890 lossG: 3.227955
[99: 799/897] train lossD: 0.267519 lossG: 1.912131
[99: 800/897] train lossD: 0.221475 lossG: 5.643398
[99: 801/897] train lossD: 0.273649 lossG: 3.708673
[99: 802/897] train lossD: 0.167975 lossG: 2.771126
[99: 803/897] train lossD: 0.095470 lossG: 4.696949
[99: 804/897] train lossD: 0.164074 lossG: 2.466290
[99: 805/897] train lossD: 0.084150 lossG: 3.851753
[99: 806/897] train lossD: 0.078557 lossG: 3.429450
[99: 807/897] train lossD: 0.084649 lossG: 3.465409
[99: 808/897] train lossD: 0.174265 lossG: 3.385497
[99: 809/897] train lossD: 0.086615 lossG: 2.722601
[99: 810/897

In [43]:
gen.eval()
with torch.no_grad():
    z = Variable(torch.cuda.FloatTensor(np.random.normal(0, 1, (64, 128))))
    generated_pcd = gen(z)

In [47]:
pcd = generated_pcd[60]
points = pcd.permute(1,0).cpu().detach().numpy()
pcd  = o3d.geometry.PointCloud()
points = o3d.utility.Vector3dVector(points) 
pcd.points = points
# Visualize the point cloud within open3d
o3d.visualization.draw_geometries([pcd]) 

In [ ]:
generator.eval()
with torch.no_grad():
    z = Variable(Tensor(np.random.normal(0, 1, (32, 128))))
    generated_pcd = generator(z)

In [12]:
def evaluate_chamfer(xyz1, xyz2):
    xyz1 = xyz1.permute(0, 2, 1)
    xyz2 = xyz2.permute(0, 2, 1)
    distance = torch.cdist(xyz1, xyz2)
    dist1, idx1 = distance.min(2)
    dist2, idx2 = distance.min(1)
    loss = (dist1 ** 2).mean() + (dist2 ** 2).mean()
    return loss

In [ ]:
dist1, idx1, dist2, idx2 = chamfer_distance(src.unsqueeze(0), tgt.unsqueeze(0))
# loss = dist1.mean() + dist2.mean()
loss = (dist1 ** 2).mean() + (dist2 ** 2).mean()

In [16]:
generator = gen
Tensor = torch.cuda.FloatTensor
generator.eval()
with torch.no_grad():
    for i, (imgs) in enumerate(train_loader):
        real_imgs = Variable(imgs.type(Tensor))
        z = Variable(Tensor(np.random.normal(0, 1, (32, 128))))
        fake_imgs = generator(z)
        break
    metric = evaluate_chamfer(real_imgs, fake_imgs)
    generator.train()

In [29]:
xyz1 = real_imgs
xyz2 =fake_imgs
distance = torch.cdist(xyz1, xyz2)
dist1, idx1 = distance.min(2)
dist2, idx2 = distance.min(1)
loss = (dist1 ** 2).mean() + (dist2 ** 2).mean()

In [23]:
model_dict = {'D': discriminator.state_dict(), 'D_O': optimizer_D.state_dict(), 'G': generator.state_dict(), 'G_O': optimizer_G.state_dict()}

In [24]:
torch.save(model_dict, 'PGAN_20.pt')